In [1]:
%run sinkHornSudokuUtils.ipynb

In [2]:
import numpy as np

In [3]:
def getAllCons(su):
    allC = {}
    N = len(su)
    for r in range(N):
        for c in range(N):
            cons = [0]*N
            if su[r][c] != 0:
                cons[su[r][c] - 1] = 1
            else:
                cons = [1]*N
                #print(r, c, cons)
                #check row:
                for col in range(N):
                    if su[r][col] > 0:
                        cons[su[r][col] - 1] = 0
                #check col:
                #print("After row",r, c, cons)
                for row in range(N):
                    if su[row][c] > 0:
                        cons[su[row][c] - 1] = 0
                #print("After col",r, c, cons)
                #check block
                rS = int(r/n)*n
                cS = int(c/n)*n
                for row in range(rS, rS + n):
                    for col in range(cS, cS + n):
                        if su[row][col] > 0:
                            cons[su[row][col] - 1] = 0
                #print("After block",r, c, cons)
                s = sum(cons)
                #
                for i in range(N):
                    cons[i] /= s
            allC[str(r) + "_" + str(c)] = cons
    return allC

In [4]:
def getRowCons(allC):
    N = 9
    rowC = []
    for r in range(N):
        rowT =[]
        for c in range(N):
            rowT.append(allC[str(r) + "_" + str(c)])
        rowC.append(np.array(rowT))
    return rowC

def updateConsFromRow(rowC, allC):
    N = 9
    for r in range(N):
        for c in range(N):
            allC[str(r) + "_" + str(c)] = rowC[r][c]

In [5]:
def getColCons(allC):
    N = 9
    colC = []
    for r in range(N):
        colT =[]
        for c in range(N):
            colT.append(allC[str(c) + "_" + str(r)])
        colC.append(np.array(colT))
    return colC
    
def updateConsFromCol(colC, allC):
    N = 9
    for r in range(N):
        for c in range(N):
            allC[str(c) + "_" + str(r)] = colC[r][c]

In [6]:
def getBlockCons(allC):
    n = 3
    blockC = []
    for i in range(n):
        for j in range(n):
            temp = []
            for r in range(i*n, i*n + n):
                for c in range(j*n, j*n + n):
                    temp.append(allC[str(r) + "_" + str(c)])
            blockC.append(np.array(temp))
    return blockC
    
def updateConsFromBlock(blockC, allC):
    n = 3
    for i in range(n):
        for j in range(n):
            for r in range(i*n, i*n + n):
                for c in range(j*n, j*n + n):
                    allC[str(r) + "_" + str(c)] = blockC[i*n + j][ (r-i*n)*n + (c-j*n)]

In [7]:
def getRCBCons_(rowC, colC, blockC, allC):
    for r in range(N):
        rowT =[]
        colT = []
        for c in range(N):
            rowT.append(allC[str(r) + "_" + str(c)])
            colT.append(allC[str(c) + "_" + str(r)])
        rowC.append(np.array(rowT))
        colC.append(np.array(colT))

    for i in range(n):
        for j in range(n):
            temp = []
            for r in range(i*n, i*n + n):
                for c in range(j*n, j*n + n):
                    temp.append(allC[str(r) + "_" + str(c)])
            blockC.append(np.array(temp))

In [8]:
def getMaxIdx(npArr):
    maxI = 0
    maxV = npArr[maxI]
    for idx in range(1, len(npArr)):
        if npArr[idx] == maxV:
            maxI = -1    #We have multiple indexes with same max value, so no winner
            continue
        if npArr[idx] > maxV:
            maxI = idx
            maxV = npArr[idx]
    return maxI

In [9]:
#printM(rowC[0])

In [10]:
#rowC[0][2]

In [12]:
#su = getSudoku("ipSudo2Medium.txt")
#su = getSudoku("ipSudo3Easy.txt")
su = getSudoku("halt.txt")

printM(su, True)
N = 9
n = 3
rowC = []
colC = []
blockC = []

cutoff = 0.8
rowC = []
colC = []
blockC = []
allC = getAllCons(su)
for itr in range(100000):
    #cutoff -= 0.05
    
    #getRCBCons(rowC, colC, blockC, allC)
    #if True:
    #    break
    #Now first to SB to all matricies.
    rowC = getRowCons(allC)
    for i in range(N):
        rowC[i] = SB(rowC[i])
    updateConsFromRow(rowC, allC)
    #
    colC = getColCons(allC)
    for i in range(N):
        colC[i] = SB(colC[i])
    updateConsFromCol(colC, allC)
    #
    blockC = getBlockCons(allC)
    for i in range(N):
        blockC[i] = SB(blockC[i])
    updateConsFromBlock(blockC, allC)
    #
    #    
    #
    someLeft = False
    solved = 0
    #Now loop through row and column.
    for r in range(N):
        for c in range(N):
            if su[r][c] != 0:
                continue
            rC4V = rowC[r][c]
            cC4V = colC[c][r]
            bC4V = blockC[ int(r/n)*n + int(c/n)][(r%n)*n + (c%n)]
            #Find the value from each constraint. If all have values and the values are same (no ties) then choose
            #that and update the constraint (set that p to 1)
            maxI = getMaxIdx(rC4V)
            if maxI < 0 or rC4V[maxI] < cutoff:
                someLeft = True
                continue
            tmpI = getMaxIdx(cC4V)
            if tmpI < 0 or tmpI != maxI or cC4V[maxI] < cutoff:
                someLeft = True
                continue
            tmpI = getMaxIdx(bC4V)
            if tmpI < 0 or tmpI != maxI or bC4V[maxI] < cutoff:
                someLeft = True
                continue
            solved += 1
            print("[",r,"][",c,"]: ", (maxI + 1))
            su[r][c] = maxI + 1
            for i in range(N):
                if i == maxI:
                    rowC[r][c][i] = 1
                    colC[c][r][i] = 1
                    blockC[ int(r/n)*n + int(c/n)][(r%n)*n + (c%n)][i] = 1
                else:
                    rowC[r][c][i] = 0
                    colC[c][r][i] = 0
                    blockC[ int(r/n)*n + int(c/n)][(r%n)*n + (c%n)][i] = 0
    #Also keep track of how many values are filled.
    if solved == 0:
        print("Nothing solved... for itr: ",itr)
        #break
    else:
        print("\nSolved at, ", itr,": ",solved," Now the sudoku is:")
        printM(su, True)
    #If all N*N are filled. Hurrey!!! Break.
    if not someLeft:
        break


-------------------------------------------
 | 0  0  3   | 0  0  9   | 0  8  1  
 | 0  0  0   | 2  0  0   | 0  6  0  
 | 5  0  0   | 0  1  0   | 7  0  0  
-------------------------------------------
 | 8  9  0   | 0  0  0   | 0  0  0  
 | 0  0  5   | 6  0  1   | 2  0  0  
 | 0  0  0   | 0  0  0   | 0  3  7  
-------------------------------------------
 | 0  0  9   | 0  2  0   | 0  0  8  
 | 0  7  0   | 0  0  4   | 0  0  0  
 | 2  5  0   | 8  0  0   | 6  0  0  Nothing solved... for itr:  0
[ 0 ][ 1 ]:  2
[ 3 ][ 8 ]:  6
[ 4 ][ 4 ]:  8
[ 5 ][ 6 ]:  8
[ 7 ][ 2 ]:  8

Solved at,  1 :  5  Now the sudoku is:

-------------------------------------------
 | 0  2  3   | 0  0  9   | 0  8  1  
 | 0  0  0   | 2  0  0   | 0  6  0  
 | 5  0  0   | 0  1  0   | 7  0  0  
-------------------------------------------
 | 8  9  0   | 0  0  0   | 0  0  6  
 | 0  0  5   | 6  8  1   | 2  0  0  
 | 0  0  0   | 0  0  0   | 8  3  7  
-------------------------------------------
 | 0  0  9   | 0  2  0   | 0  0  8 

Nothing solved... for itr:  112
Nothing solved... for itr:  113
Nothing solved... for itr:  114
Nothing solved... for itr:  115
Nothing solved... for itr:  116
Nothing solved... for itr:  117
Nothing solved... for itr:  118
Nothing solved... for itr:  119
Nothing solved... for itr:  120
Nothing solved... for itr:  121
Nothing solved... for itr:  122
Nothing solved... for itr:  123
Nothing solved... for itr:  124
Nothing solved... for itr:  125
Nothing solved... for itr:  126
Nothing solved... for itr:  127
Nothing solved... for itr:  128
Nothing solved... for itr:  129
Nothing solved... for itr:  130
Nothing solved... for itr:  131
Nothing solved... for itr:  132
Nothing solved... for itr:  133
Nothing solved... for itr:  134
Nothing solved... for itr:  135
Nothing solved... for itr:  136
Nothing solved... for itr:  137
Nothing solved... for itr:  138
Nothing solved... for itr:  139
Nothing solved... for itr:  140
Nothing solved... for itr:  141
Nothing solved... for itr:  142
Nothing 

Nothing solved... for itr:  373
Nothing solved... for itr:  374
Nothing solved... for itr:  375
Nothing solved... for itr:  376
Nothing solved... for itr:  377
Nothing solved... for itr:  378
Nothing solved... for itr:  379
Nothing solved... for itr:  380
Nothing solved... for itr:  381
Nothing solved... for itr:  382
Nothing solved... for itr:  383
Nothing solved... for itr:  384
Nothing solved... for itr:  385
Nothing solved... for itr:  386
Nothing solved... for itr:  387
Nothing solved... for itr:  388
Nothing solved... for itr:  389
Nothing solved... for itr:  390
Nothing solved... for itr:  391
Nothing solved... for itr:  392
Nothing solved... for itr:  393
Nothing solved... for itr:  394
Nothing solved... for itr:  395
Nothing solved... for itr:  396
Nothing solved... for itr:  397
Nothing solved... for itr:  398
Nothing solved... for itr:  399
Nothing solved... for itr:  400
Nothing solved... for itr:  401
Nothing solved... for itr:  402
Nothing solved... for itr:  403
Nothing 

Nothing solved... for itr:  644
Nothing solved... for itr:  645
Nothing solved... for itr:  646
Nothing solved... for itr:  647
Nothing solved... for itr:  648
Nothing solved... for itr:  649
Nothing solved... for itr:  650
Nothing solved... for itr:  651
Nothing solved... for itr:  652
Nothing solved... for itr:  653
Nothing solved... for itr:  654
Nothing solved... for itr:  655
Nothing solved... for itr:  656
Nothing solved... for itr:  657
Nothing solved... for itr:  658
Nothing solved... for itr:  659
Nothing solved... for itr:  660
Nothing solved... for itr:  661
Nothing solved... for itr:  662
Nothing solved... for itr:  663
Nothing solved... for itr:  664
Nothing solved... for itr:  665
Nothing solved... for itr:  666
Nothing solved... for itr:  667
Nothing solved... for itr:  668
Nothing solved... for itr:  669
Nothing solved... for itr:  670
Nothing solved... for itr:  671
Nothing solved... for itr:  672
Nothing solved... for itr:  673
Nothing solved... for itr:  674
Nothing 

Nothing solved... for itr:  937
Nothing solved... for itr:  938
Nothing solved... for itr:  939
Nothing solved... for itr:  940
Nothing solved... for itr:  941
Nothing solved... for itr:  942
Nothing solved... for itr:  943
Nothing solved... for itr:  944
Nothing solved... for itr:  945
Nothing solved... for itr:  946
Nothing solved... for itr:  947
Nothing solved... for itr:  948
Nothing solved... for itr:  949
Nothing solved... for itr:  950
Nothing solved... for itr:  951
Nothing solved... for itr:  952
Nothing solved... for itr:  953
Nothing solved... for itr:  954
Nothing solved... for itr:  955
Nothing solved... for itr:  956
Nothing solved... for itr:  957
Nothing solved... for itr:  958
Nothing solved... for itr:  959
Nothing solved... for itr:  960
Nothing solved... for itr:  961
Nothing solved... for itr:  962
Nothing solved... for itr:  963
Nothing solved... for itr:  964
Nothing solved... for itr:  965
Nothing solved... for itr:  966
Nothing solved... for itr:  967
Nothing 

...

Nothing solved... for itr:  98764
Nothing solved... for itr:  98765
Nothing solved... for itr:  98766
Nothing solved... for itr:  98767
Nothing solved... for itr:  98768
Nothing solved... for itr:  98769
Nothing solved... for itr:  98770
Nothing solved... for itr:  98771
Nothing solved... for itr:  98772
Nothing solved... for itr:  98773
Nothing solved... for itr:  98774
Nothing solved... for itr:  98775
Nothing solved... for itr:  98776
Nothing solved... for itr:  98777
Nothing solved... for itr:  98778
Nothing solved... for itr:  98779
Nothing solved... for itr:  98780
Nothing solved... for itr:  98781
Nothing solved... for itr:  98782
Nothing solved... for itr:  98783
Nothing solved... for itr:  98784
Nothing solved... for itr:  98785
Nothing solved... for itr:  98786
Nothing solved... for itr:  98787
Nothing solved... for itr:  98788
Nothing solved... for itr:  98789
Nothing solved... for itr:  98790
Nothing solved... for itr:  98791
Nothing solved... for itr:  98792
Nothing solved

Nothing solved... for itr:  99012
Nothing solved... for itr:  99013
Nothing solved... for itr:  99014
Nothing solved... for itr:  99015
Nothing solved... for itr:  99016
Nothing solved... for itr:  99017
Nothing solved... for itr:  99018
Nothing solved... for itr:  99019
Nothing solved... for itr:  99020
Nothing solved... for itr:  99021
Nothing solved... for itr:  99022
Nothing solved... for itr:  99023
Nothing solved... for itr:  99024
Nothing solved... for itr:  99025
Nothing solved... for itr:  99026
Nothing solved... for itr:  99027
Nothing solved... for itr:  99028
Nothing solved... for itr:  99029
Nothing solved... for itr:  99030
Nothing solved... for itr:  99031
Nothing solved... for itr:  99032
Nothing solved... for itr:  99033
Nothing solved... for itr:  99034
Nothing solved... for itr:  99035
Nothing solved... for itr:  99036
Nothing solved... for itr:  99037
Nothing solved... for itr:  99038
Nothing solved... for itr:  99039
Nothing solved... for itr:  99040
Nothing solved

Nothing solved... for itr:  99276
Nothing solved... for itr:  99277
Nothing solved... for itr:  99278
Nothing solved... for itr:  99279
Nothing solved... for itr:  99280
Nothing solved... for itr:  99281
Nothing solved... for itr:  99282
Nothing solved... for itr:  99283
Nothing solved... for itr:  99284
Nothing solved... for itr:  99285
Nothing solved... for itr:  99286
Nothing solved... for itr:  99287
Nothing solved... for itr:  99288
Nothing solved... for itr:  99289
Nothing solved... for itr:  99290
Nothing solved... for itr:  99291
Nothing solved... for itr:  99292
Nothing solved... for itr:  99293
Nothing solved... for itr:  99294
Nothing solved... for itr:  99295
Nothing solved... for itr:  99296
Nothing solved... for itr:  99297
Nothing solved... for itr:  99298
Nothing solved... for itr:  99299
Nothing solved... for itr:  99300
Nothing solved... for itr:  99301
Nothing solved... for itr:  99302
Nothing solved... for itr:  99303
Nothing solved... for itr:  99304
Nothing solved

Nothing solved... for itr:  99562
Nothing solved... for itr:  99563
Nothing solved... for itr:  99564
Nothing solved... for itr:  99565
Nothing solved... for itr:  99566
Nothing solved... for itr:  99567
Nothing solved... for itr:  99568
Nothing solved... for itr:  99569
Nothing solved... for itr:  99570
Nothing solved... for itr:  99571
Nothing solved... for itr:  99572
Nothing solved... for itr:  99573
Nothing solved... for itr:  99574
Nothing solved... for itr:  99575
Nothing solved... for itr:  99576
Nothing solved... for itr:  99577
Nothing solved... for itr:  99578
Nothing solved... for itr:  99579
Nothing solved... for itr:  99580
Nothing solved... for itr:  99581
Nothing solved... for itr:  99582
Nothing solved... for itr:  99583
Nothing solved... for itr:  99584
Nothing solved... for itr:  99585
Nothing solved... for itr:  99586
Nothing solved... for itr:  99587
Nothing solved... for itr:  99588
Nothing solved... for itr:  99589
Nothing solved... for itr:  99590
Nothing solved

Nothing solved... for itr:  99832
Nothing solved... for itr:  99833
Nothing solved... for itr:  99834
Nothing solved... for itr:  99835
Nothing solved... for itr:  99836
Nothing solved... for itr:  99837
Nothing solved... for itr:  99838
Nothing solved... for itr:  99839
Nothing solved... for itr:  99840
Nothing solved... for itr:  99841
Nothing solved... for itr:  99842
Nothing solved... for itr:  99843
Nothing solved... for itr:  99844
Nothing solved... for itr:  99845
Nothing solved... for itr:  99846
Nothing solved... for itr:  99847
Nothing solved... for itr:  99848
Nothing solved... for itr:  99849
Nothing solved... for itr:  99850
Nothing solved... for itr:  99851
Nothing solved... for itr:  99852
Nothing solved... for itr:  99853
Nothing solved... for itr:  99854
Nothing solved... for itr:  99855
Nothing solved... for itr:  99856
Nothing solved... for itr:  99857
Nothing solved... for itr:  99858
Nothing solved... for itr:  99859
Nothing solved... for itr:  99860
Nothing solved

In [13]:
printM(su, True)


-------------------------------------------
 | 0  2  3   | 0  0  9   | 0  8  1  
 | 9  1  7   | 2  0  8   | 0  6  0  
 | 5  8  0   | 0  1  0   | 7  0  0  
-------------------------------------------
 | 8  9  0   | 0  0  0   | 0  0  6  
 | 7  3  5   | 6  8  1   | 2  0  0  
 | 1  0  0   | 9  0  0   | 8  3  7  
-------------------------------------------
 | 0  0  9   | 0  2  0   | 0  0  8  
 | 0  7  8   | 0  0  4   | 9  0  0  
 | 2  5  1   | 8  9  0   | 6  0  0  